## 原始数据分析

查看数据长度分布

In [20]:
import pandas as pd
len_list = []
file_list = ['test', 'train', 'val']
for file in file_list:
    with open(f'../data/{file}/sentences.txt', 'r', encoding='utf-8') as f:
        len_list += [len(line.strip().split(' ')) for line in f]
print(pd.Series(len_list).describe(percentiles=[.25, .5, .75, .85, .95]))

count    1887.000000
mean      410.542660
std       160.677229
min       172.000000
25%       307.000000
50%       374.000000
75%       483.000000
85%       549.100000
95%       700.800000
max      1664.000000
dtype: float64


分类别实体长度

In [22]:
data_dir = ['../data/train/', '../data/val/']
sentences = []
tags = []
for dir_ in data_dir:
    with open(dir_+'sentences.txt', 'r', encoding='utf-8') as f_sen,\
        open(dir_+'tags.txt', 'r', encoding='utf-8') as f_tag:
        sentences.extend([line.strip().split(' ') for line in f_sen])
        tags.extend([line.strip().split(' ') for line in f_tag])

In [23]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con)))
    y_true.extend(sample) 

In [24]:
y_true

[('解剖部位', '中下腹'),
 ('解剖部位', '腹'),
 ('解剖部位', '腹'),
 ('疾病和诊断', '慢性胃窦炎'),
 ('药物', '吗丁啉'),
 ('解剖部位', '胃'),
 ('解剖部位', '下腹'),
 ('药物', '奥美拉唑'),
 ('药物', '依替米星'),
 ('药物', '复合磷酸氢钾'),
 ('解剖部位', '腹'),
 ('解剖部位', '腹'),
 ('解剖部位', '腹'),
 ('解剖部位', '胸骨'),
 ('解剖部位', '腹'),
 ('实验室检验', '幽门螺旋杆菌抗体'),
 ('影像检查', '心电图'),
 ('疾病和诊断', '窦性心律'),
 ('影像检查', '心电图'),
 ('疾病和诊断', '慢性胃炎'),
 ('疾病和诊断', '结肠息肉'),
 ('手术', '结肠息肉内镜上切除'),
 ('疾病和诊断', '肠息肉'),
 ('疾病和诊断', '直肠癌'),
 ('手术', '腹腔镜上直肠全系膜切除术(TME)预防性回肠造口术'),
 ('疾病和诊断', '肠溃疡型管状腺癌II级'),
 ('解剖部位', '肠周淋巴结'),
 ('疾病和诊断', '直肠癌术后'),
 ('解剖部位', '腹'),
 ('解剖部位', '腹'),
 ('解剖部位', '咽'),
 ('药物', '头孢呋辛'),
 ('解剖部位', '四肢'),
 ('影像检查', '头颅CT'),
 ('影像检查', '胸部CT'),
 ('解剖部位', '右侧顶部蛛网膜上腔'),
 ('疾病和诊断', '脑萎缩'),
 ('疾病和诊断', '两上肺感染'),
 ('解剖部位', '纵膈'),
 ('解剖部位', '两侧胸膜'),
 ('实验室检验', '酸碱度'),
 ('实验室检验', '二氧化碳分压'),
 ('实验室检验', '碱剩余'),
 ('实验室检验', '高敏肌钙蛋白T'),
 ('实验室检验', '白细胞'),
 ('实验室检验', '中性粒细胞绝对值'),
 ('实验室检验', '超敏C反应蛋白'),
 ('药物', '脑苷激肽'),
 ('药物', '神经节苷脂'),
 ('药物', '甘露醇'),
 ('药物', '奥美拉唑'),
 ('药物', '清开灵'),
 ('药物',

In [25]:
import pandas as pd
df = pd.DataFrame({
    "type": [ne[0] for ne in y_true],
    "content": [ne[1] for ne in y_true]
})
df['length'] = df.apply(lambda row: len(row.content), axis=1)

In [26]:
df

type content  length
0       解剖部位     中下腹       3
1       解剖部位       腹       1
2       解剖部位       腹       1
3      疾病和诊断   慢性胃窦炎       5
4         药物     吗丁啉       3
...      ...     ...     ...
27448   解剖部位      腹腔       2
27449     药物     紫杉醇       3
27450     药物     紫杉醇       3
27451     药物      特素       2
27452     药物    奥沙利铂       4

[27453 rows x 3 columns]

In [27]:
# 按类别分组
df_gb = df.groupby('type')

In [29]:
df_lab = df.iloc[df_gb.groups['实验室检验']]

长度为1的实验室检验实体

In [38]:
df_lab[df_lab.length==1].content.unique()

array(['钾', '钠', '氯', 'N', 'K', 'L', 'e', '钙', '磷', '腹'], dtype=object)

In [230]:
df_gb["length"].mean()

type
实验室检验     3.974885
影像检查      3.774173
手术       12.678280
疾病和诊断     6.939712
药物        3.738430
解剖部位      2.421670
Name: length, dtype: float64

In [294]:
from numpy import mean
mean(df_gb["length"].mean().tolist())

5.587858134606091

In [231]:
from collections import Counter

In [232]:
sorted(Counter(df.loc[df_gb.groups['解剖部位']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 6113),
 (2, 3156),
 (3, 1618),
 (4, 860),
 (5, 547),
 (6, 416),
 (7, 153),
 (8, 154),
 (9, 67),
 (10, 68),
 (11, 42),
 (12, 24),
 (13, 26),
 (14, 9),
 (15, 8),
 (16, 2),
 (17, 1),
 (18, 2),
 (19, 5),
 (20, 5),
 (21, 2),
 (22, 1),
 (23, 3),
 (24, 3),
 (26, 3),
 (27, 3),
 (28, 1),
 (29, 2),
 (30, 2),
 (31, 2),
 (32, 2),
 (33, 1),
 (34, 1),
 (36, 1),
 (37, 1),
 (38, 1),
 (40, 1),
 (48, 1),
 (53, 1),
 (125, 1)]

In [233]:
sorted(Counter(df.loc[df_gb.groups['药物']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(2, 358),
 (3, 1075),
 (4, 1011),
 (5, 224),
 (6, 91),
 (7, 89),
 (8, 28),
 (9, 27),
 (10, 9),
 (11, 1),
 (12, 1),
 (17, 3)]

In [234]:
sorted(Counter(df.loc[df_gb.groups['疾病和诊断']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 7),
 (2, 341),
 (3, 913),
 (4, 914),
 (5, 1028),
 (6, 762),
 (7, 553),
 (8, 369),
 (9, 283),
 (10, 218),
 (11, 176),
 (12, 168),
 (13, 105),
 (14, 78),
 (15, 67),
 (16, 77),
 (17, 44),
 (18, 54),
 (19, 42),
 (20, 37),
 (21, 20),
 (22, 16),
 (23, 20),
 (24, 17),
 (25, 14),
 (26, 11),
 (27, 7),
 (28, 8),
 (29, 1),
 (30, 4),
 (31, 6),
 (32, 2),
 (33, 4),
 (34, 2),
 (35, 1),
 (36, 5),
 (37, 2),
 (38, 1),
 (39, 2),
 (43, 1),
 (44, 2),
 (46, 1),
 (49, 1),
 (56, 1),
 (92, 1)]

In [235]:
sorted(Counter(df.loc[df_gb.groups['实验室检验']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 72),
 (2, 315),
 (3, 624),
 (4, 315),
 (5, 303),
 (6, 144),
 (7, 66),
 (8, 63),
 (9, 11),
 (10, 12),
 (11, 15),
 (12, 2),
 (13, 2),
 (14, 1),
 (16, 3),
 (20, 1),
 (28, 1),
 (32, 1)]

In [236]:
sorted(Counter(df.loc[df_gb.groups['影像检查']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(2, 510),
 (3, 160),
 (4, 479),
 (5, 167),
 (6, 132),
 (7, 54),
 (8, 11),
 (9, 6),
 (10, 9),
 (11, 4),
 (12, 4),
 (13, 2),
 (14, 1),
 (15, 1),
 (16, 1)]

In [237]:
sorted(Counter(df.loc[df_gb.groups['手术']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(2, 3),
 (3, 21),
 (4, 71),
 (5, 119),
 (6, 88),
 (7, 140),
 (8, 128),
 (9, 77),
 (10, 90),
 (11, 64),
 (12, 57),
 (13, 43),
 (14, 60),
 (15, 38),
 (16, 31),
 (17, 31),
 (18, 46),
 (19, 19),
 (20, 20),
 (21, 14),
 (22, 13),
 (23, 21),
 (24, 12),
 (25, 17),
 (26, 19),
 (27, 8),
 (28, 8),
 (29, 7),
 (30, 11),
 (31, 6),
 (32, 6),
 (33, 4),
 (34, 9),
 (35, 6),
 (36, 6),
 (37, 3),
 (38, 6),
 (39, 2),
 (40, 5),
 (41, 2),
 (42, 4),
 (43, 4),
 (47, 1),
 (48, 2),
 (49, 2),
 (51, 1),
 (53, 2),
 (55, 1),
 (84, 1)]

分类别实体个数

In [238]:
df_gb.count()

content  length
type                  
实验室检验     1951    1951
影像检查      1541    1541
手术        1349    1349
疾病和诊断     6386    6386
药物        2917    2917
解剖部位     13309   13309

取出长度大于10的手术和诊断实体

In [41]:
df_ope = df.iloc[df_gb.groups['手术']]

In [56]:
ope_ll = df_ope[df_ope.length >= 10].content.unique().tolist()

In [51]:
df_dis = df.iloc[df_gb.groups['疾病和诊断']]

In [57]:
dis_ll = df_dis[df_dis.length >= 10].content.unique().tolist()

In [58]:
with open('./long_vocab.txt', 'w', encoding='utf-8') as f:
    for line in ope_ll:
        f.write(f'手术\t{line}\n')
    for line in dis_ll:
        f.write(f'疾病和诊断\t{line}\n')

## 2019data

In [188]:
with open('../data/pseudo/2019data.txt', 'r', encoding='utf-8') as f:
    data_src_li = [dict(eval(line.strip())) for line in f]

In [190]:
data_src_li[0]['entities'][0]

{'end_pos': 15, 'label_type': '解剖部位', 'start_pos': 14}

In [195]:
with open('./extra_data.txt', 'w', encoding='utf-8') as w:
    for sample in data_src_li:
        json.dump({
            "originalText": sample['originalText'],
            "entities": [{'label_type':s['label_type'], 'start_pos':s['start_pos'], 'end_pos':s['end_pos']} if 'overlap' in s.keys() else s for s in sample['entities']]
        }, w, ensure_ascii=False)
        w.write('\n')

In [196]:
with open('../ccks2020_2_task1_train/task1_train.txt', 'r', encoding='utf-8') as f:
    data_src_li = [dict(eval(line.strip())) for line in f]

In [216]:
final_train_data = []
for d in data_src_li:
    if d not in final_train_data:
        final_train_data.append(d)

In [217]:
final_train_data

[{'originalText': '缘于入院前1月余因“胆石症、急性胆囊炎”就诊我院，下腹部CT示：1、胆总管上段多发结石，伴肝内外胆管扩张。2、急性胆囊炎，胆囊多发结石。入院后予抗感染，保肝，抑制胰酶分泌，营养支持等治疗，于2014.01.16在B超定位上行“胆囊穿刺造瘘术”，术顺，术后症状好转，家属要求出院。此次为行进一步治疗再次就诊我院，门诊拟“胆石症PTCD术后”收入院，自发病以来神志清，精神不振，饮食少，睡眠可，二便正常，体重未见明显增减。',
  'entities': [{'start_pos': 10, 'end_pos': 13, 'label_type': '疾病和诊断'},
   {'start_pos': 14, 'end_pos': 19, 'label_type': '疾病和诊断'},
   {'start_pos': 25, 'end_pos': 30, 'label_type': '影像检查'},
   {'start_pos': 34, 'end_pos': 43, 'label_type': '疾病和诊断'},
   {'start_pos': 45, 'end_pos': 52, 'label_type': '疾病和诊断'},
   {'start_pos': 55, 'end_pos': 60, 'label_type': '疾病和诊断'},
   {'start_pos': 61, 'end_pos': 67, 'label_type': '疾病和诊断'},
   {'start_pos': 77, 'end_pos': 78, 'label_type': '解剖部位'},
   {'start_pos': 81, 'end_pos': 82, 'label_type': '解剖部位'},
   {'start_pos': 106, 'end_pos': 108, 'label_type': '影像检查'},
   {'start_pos': 113, 'end_pos': 120, 'label_type': '手术'},
   {'start_pos': 159, 'end_pos': 168, 'label_type': '疾病和诊断'}]},
 {'originalText': '患者20+年前受凉后出现咳嗽、喘累

In [ ]:
for s in final_train_data:
    if s['']

In [199]:
len(final_train_data)

1587

In [209]:
# text = [d['originalText'] for d in final_train_data]
while len(final_train_data) != 0:
    d = final_train_data.pop()
    if d['originalText'] in [dd['originalText'] for dd in final_train_data]:
        print('first_ll:', d['entities'])
        
        others = [dd for dd in final_train_data if dd['originalText'] == d['originalText']]
        for dd in others:
            print('second_ll:', dd['entities'])
            print(dd)

first_ll: [{'start_pos': 36, 'end_pos': 37, 'label_type': '解剖部位'}, {'start_pos': 39, 'end_pos': 40, 'label_type': '解剖部位'}, {'start_pos': 82, 'end_pos': 88, 'label_type': '疾病和诊断'}, {'start_pos': 98, 'end_pos': 121, 'label_type': '疾病和诊断'}, {'start_pos': 130, 'end_pos': 137, 'label_type': '手术'}, {'start_pos': 157, 'end_pos': 158, 'label_type': '解剖部位'}, {'start_pos': 160, 'end_pos': 161, 'label_type': '解剖部位'}]
second_ll: [{'start_pos': 36, 'end_pos': 37, 'label_type': '解剖部位'}, {'start_pos': 39, 'end_pos': 40, 'label_type': '解剖部位'}, {'start_pos': 82, 'end_pos': 88, 'label_type': '疾病和诊断'}, {'start_pos': 98, 'end_pos': 109, 'label_type': '疾病和诊断'}, {'start_pos': 110, 'end_pos': 121, 'label_type': '疾病和诊断'}, {'start_pos': 130, 'end_pos': 137, 'label_type': '手术'}, {'start_pos': 157, 'end_pos': 158, 'label_type': '解剖部位'}, {'start_pos': 160, 'end_pos': 161, 'label_type': '解剖部位'}]
{'originalText': '患者半年前无明显诱因发现便中带血，呈鲜红色，大便成形，不伴里急后重感，无腹痛、腹泻，恶心呕吐等不适，此后下述症状持续存在，未系统诊治。10天前我院门诊行肠镜检查示“结肠多发息肉”，行病理检查示：“横结肠增

In [218]:
len(final_train_data)

1587

In [142]:
import pandas as pd

In [152]:
df = pd.DataFrame(data_src_li)

In [131]:
len(data_src_li)

2879

In [129]:
len(set(data_src_li))

1586

In [110]:
with open('../data/pseudo/2019data.txt', 'r', encoding='utf-8') as f:
    data_2019 = [dict(eval(line.strip()))['originalText'] for line in f]

In [111]:
count = 0
for d_2019 in data_2019:
    if d_2019 in data_src_li:
        count += 1
#         print('in')
#     else:
#         id_list.append()
print(count)

387


In [120]:
count = 0
for d_src in data_src_li:
#     print(d_src)
    if d_src in data_2019:
#     if d_2019 in data_src_li:
        count += 1
#         print('in')
#     else:
#         id_list.append()
print(count)

2284


## 训练集

In [274]:
train_data_dir = [Path('../data/train/'), Path('../data/val/')]

In [275]:
sentences = []
tags = []
for _dir in train_data_dir:
    with open(_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen,\
        open(_dir/'tags.txt', 'r', encoding='utf-8') as f_tag:
        sentences.extend([line.strip().split(' ') for line in f_sen])
        tags.extend([line.strip().split(' ') for line in f_tag])

In [276]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con), entity[1], entity[2]+1))
    y_true.append(sample) 

In [286]:
counters = Counter([en[:2] for sample in y_true for en in sample]).most_common()

In [287]:
with open('./en_freq.txt', 'w', encoding='utf-8') as f:
    for line in counters:
        f.write(f'{line[0][0]}\t{line[0][1]}\t{line[1]}\n')

In [242]:
for sen, true in zip(sentences, y_true):
    print("".join(sen))
    print('-*-'*40)
    print(sorted(true, key=lambda x: x[2]))
    print('\n')

患者3年前无明显诱因反复出现反酸、中下腹不适，伴有恶心、嗳气，无呕吐、吞咽困难，无烧心，无腹痛、腹泻，曾行胃镜检查提示“慢性胃窦炎”（具体不详）。自服“吗丁啉”后症状缓解。1天前患者进食火锅及少量饮酒后感明显恶心、反酸，呕吐１次，为酸臭味胃内容物，量约250ML，伴下腹间断性隐痛。遂于我院就诊，门诊予以“奥美拉唑、依替米星、复合磷酸氢钾”静脉输液治疗后症状有所缓解，今为求进一步诊治，遂拟“呕吐待查”收入我科。\U0004✄✄✄患者本次发　病以来，食欲可，神志清，精神可，睡眠不佳，大便如常，小便如常，体重无明显变化。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '中下腹', 17, 20), ('解剖部位', '腹', 45, 46), ('解剖部位', '腹', 48, 49), ('疾病和诊断', '慢性胃窦炎', 60, 65), ('药物', '吗丁啉', 76, 79), ('解剖部位', '胃', 119, 120), ('解剖部位', '下腹', 133, 135), ('药物', '奥美拉唑', 153, 157), ('药物', '依替米星', 158, 162), ('药物', '复合磷酸氢钾', 163, 169)]


，患者2年前无明显诱因出现大便异常，为青色成形软便，约2-3次/天，无粘液脓血便，无发热，无腹痛、腹泻、腹胀，无反酸、烧心，无恶心、呕吐，无进食阻挡感及哽噎感，无胸骨后疼痛，无乏力、纳差，无呕血、黑便，无停止排便、排气、腹胀，未诊疗。患者下述症状持续存在，未诊治。为明确病情，患者20天前于我院查体中心体检，，查体示：幽门螺旋杆菌抗体阳性。为求进一步治疗就诊于我院门诊，查凝血四项、乙肝五项未见明显异常，，心电图：1.窦性心律2.大致正常心电图，建议行胃肠镜检查。患者今日于内镜室行胃肠镜检查，胃镜提示慢性胃炎，，结肠镜提示：结肠息肉，并行结肠息肉内镜上切除治疗，操作顺利，报告未回，为进一步诊治，门诊以“肠息肉”收住院。✄✄✄患者自发病以来，神志清，精神可，饮食、睡眠可，大、小便如前所述，体重近期无明显变化。
-*--*

2008年8月19日开始出现中下腹痛，主要表现为隐痛，疼痛发作无明显规律性，近期逐渐加重，不向其他身体部位放射或牵涉。伴有恶心，有呕吐胃内容物，无呕血；无黑便；有嗳气，有返酸；无腹胀；无腹泻。无发热。2009年1月13日行胃镜检查报告提示：胃角MT，胃镜活检病理报告（2009-1-14）为（胃角）腺癌。现为行进一步检查收治入院。发病以来，患者食欲渐差，大便习惯性状尚正常，小便如常，体重略有减轻。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '中下腹', 14, 17), ('解剖部位', '胃', 67, 68), ('解剖部位', '腹', 89, 90), ('解剖部位', '腹', 93, 94), ('疾病和诊断', '胃角MT', 120, 124), ('疾病和诊断', '（胃角）腺癌', 145, 151)]


入院前10+天患者无明显诱因出现下腹部阵发性烧灼样疼痛，以上午3-4点及夜间发作较多，无肩背部放射痛，与进食及体位无关。伴腹胀、嗳气，无反酸、腹泻、黑便、恶心、呕吐，无心悸、气促、胸闷、胸痛，无畏寒、发热、黄疸。在迎**医院就诊，给予口服“中药”（具体不详）后无缓解。今日遂来我院就诊，门诊查“无痛胃镜示：胃底多发性息肉，胆汁反流性胃炎，HP（+）。腹部彩超：肝实质回声细密，胆囊切除。心电图正常。”为进一步诊治，门诊以“胃底息肉，胆汁反流性胃炎”收入我科。病程中精神、饮食尚可，大小便正常，体重无明显变化。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '下腹', 16, 18), ('解剖部位', '肩背部', 44, 47), ('解剖部位', '腹', 61, 62), ('解剖部位', '腹', 71, 72), ('解剖部位', '心', 84, 85), ('解剖部位', '胸', 90, 91), ('解剖

## Badcase分析

In [2]:
from pathlib import Path

In [3]:
import sys
sys.path.insert(0, '../')

In [4]:
from metrics import get_entities
from utils import IO2STR

In [68]:
val_data_dir = Path('../data/val/')

In [69]:
with open(val_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen,\
    open(val_data_dir/'tags.txt', 'r', encoding='utf-8') as f_tag:
    sentences = [line.strip().split(' ') for line in f_sen]
    tags = [line.strip().split(' ') for line in f_tag]

获取gold label

In [70]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con), entity[1], entity[2]+1))
    y_true.append(sample) 

In [71]:
y_true

[[('解剖部位', '宫颈', 29, 31),
  ('疾病和诊断', '宫颈癌', 44, 47),
  ('手术', '广泛子宫全切+腹主动脉旁淋巴结取样+盆腔淋巴结切除+两侧卵巢悬吊', 53, 85),
  ('疾病和诊断', '中分化鳞状细胞癌', 95, 103),
  ('解剖部位', '宫颈', 123, 125),
  ('影像检查', '盆腹MRI', 157, 162),
  ('解剖部位', '阴道', 163, 165),
  ('解剖部位', '腹', 180, 181),
  ('解剖部位', '腹', 197, 198),
  ('影像检查', 'PET-CT', 215, 221),
  ('解剖部位', '阴道', 223, 225),
  ('解剖部位', '腹', 245, 246),
  ('解剖部位', '盆腔', 254, 256)],
 [('解剖部位', '胸', 164, 165),
  ('解剖部位', '头', 173, 174),
  ('疾病和诊断', '慢性阻塞性肺病急性加重', 250, 261)],
 [('解剖部位', '下腹部', 14, 17),
  ('影像检查', '彩超', 88, 90),
  ('解剖部位', '胆囊', 91, 93),
  ('解剖部位', '胆囊', 98, 100),
  ('疾病和诊断', '急性胆囊炎', 106, 111),
  ('解剖部位', '主胰管', 112, 115),
  ('疾病和诊断', '腹腔积液', 118, 122),
  ('实验室检验', '白细胞', 127, 130),
  ('实验室检验', '中性粒细胞', 143, 148),
  ('实验室检验', '白蛋白', 161, 164),
  ('实验室检验', 'AST', 171, 174),
  ('实验室检验', 'GGT', 182, 185),
  ('实验室检验', 'TBIL', 193, 197),
  ('实验室检验', 'DBIL', 208, 212),
  ('实验室检验', 'PT', 228, 230),
  ('实验室检验', '纤维蛋白原', 236, 241),
  ('实验室检验', '凝血酶', 249, 252),
  ('疾

In [98]:
import re
for sample in y_true:
    for line in sample:
        content = line[1]
#         print(content)
        if re.findall(r'[^\u4e00-\u9fa5A-Za-z]',content[-1]) != []:
            print(content)

消化道出血原因待查✄
直肠癌根治术(DIXON)
胃癌根治术\"（远端胃大部切除）
S1
CA125
胃窦腺癌（中低度分化）
腹腔镜辅助直肠癌根治术（miles术式）
NET✄G3
肝S8
胃癌根治术（远端胃大部切除+ROUX-EN-Y重建）
胃低分化腺癌（T4AN3MO,IIIC,LN+7/59）
CEA✄
CA125
S2
胃中至低分化腺癌（LAUREN，分型：混合型）
腺癌PT1N0M0
乙状结肠粘液性腺癌（中分化）
HCO3-
PACO2
PAO2
胰岛素（空腹）
胰岛素（2H）
C肽（空腹）
C肽（2H）
胰十二指肠切除术（WHIPPLE术）
十二指肠中分化腺癌（PT2N0M0）
(
肿物)
高级别鳞状下皮内瘤变（CINII）
高级别鳞状下皮内病变（CINII）
右乳浸润性导管癌（pt2n1m0,iib期三阴型）
壶腹部中分化腺癌，部分为粘液腺癌，，分期为：T3N1M0
CA19-9
CA19-9
宫体混合型腺癌（80％为II型透明细胞腺癌，20％为I型子宫内膜样腺癌）
胃体小弯腺癌（中度分化）
希罗达✄
CEA✄
根治性全胃切除术（食管空肠ROUX-Y吻合、D2+、R0)
直肠腺癌（PT2N0M0）
腹腔镜上直肠癌根治术（DIXON）
腹腔镜上直肠癌根治术（MILES）


获取pre label

In [81]:
ex1_dir = Path('./val/val_fusion.txt')

In [82]:
import json

In [83]:
with open(ex1_dir, 'r', encoding='utf-8') as f:
    pre = [json.loads(line.strip()) for line in f]

In [84]:
pre

[{'originalText': '，剖宫产术后4月（孕期体重增加20KG），常规产后检查发现宫颈病变，2014.1.29因宫颈癌行手术治疗（广泛子宫全切+腹主动脉旁淋巴结取样+盆腔淋巴结切除+两侧卵巢悬吊）。，我院会诊病理：中分化鳞状细胞癌，可见脉管癌栓，浸润深度1.4CM，累及宫颈，淋巴结无转移。患者现术后恢复良好，现大小便正常。，14-3-5盆腹MRI：阴道残端左下方不规则信号，大网膜及腹膜弥漫增厚，较大42*28MM。腹膜弥漫增厚转移可能。14-3-10PET-CT复查阴道残端及残端左侧不规则软组织影伴代谢活跃，腹膜考虑非转移，行盆腔放疗，，计划：CTV45GY/25F，2014-3-27开始放疗，放疗7次，大便次数多，2-3次/天。',
  'entities': [{'label_type': '解剖部位', 'start_pos': 180, 'end_pos': 181},
   {'label_type': '解剖部位', 'start_pos': 123, 'end_pos': 125},
   {'label_type': '解剖部位', 'start_pos': 29, 'end_pos': 31},
   {'label_type': '解剖部位', 'start_pos': 254, 'end_pos': 256},
   {'label_type': '影像检查', 'start_pos': 215, 'end_pos': 221},
   {'label_type': '影像检查', 'start_pos': 157, 'end_pos': 162},
   {'label_type': '解剖部位', 'start_pos': 163, 'end_pos': 165},
   {'label_type': '疾病和诊断', 'start_pos': 95, 'end_pos': 103},
   {'label_type': '解剖部位', 'start_pos': 223, 'end_pos': 225},
   {'label_type': '解剖部位', 'start_pos': 197, 'end_pos': 198},
   {'label_type': '解剖部位', 'start_pos': 245, 'end_po

In [85]:
y_pre = []
for s in pre:
    text = s['originalText']
    entities = s['entities']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [86]:
y_pre

[[('解剖部位', '腹', 180, 181),
  ('解剖部位', '宫颈', 123, 125),
  ('解剖部位', '宫颈', 29, 31),
  ('解剖部位', '盆腔', 254, 256),
  ('影像检查', 'PET-CT', 215, 221),
  ('影像检查', '盆腹MRI', 157, 162),
  ('解剖部位', '阴道', 163, 165),
  ('疾病和诊断', '中分化鳞状细胞癌', 95, 103),
  ('解剖部位', '阴道', 223, 225),
  ('解剖部位', '腹', 197, 198),
  ('解剖部位', '腹', 245, 246),
  ('疾病和诊断', '宫颈癌', 44, 47),
  ('疾病和诊断', '剖宫产术后', 1, 6),
  ('手术', '广泛子宫全切+腹主动脉旁淋巴结取样+盆腔淋巴结切除+两侧卵巢悬吊', 53, 85)],
 [('解剖部位', '胸', 164, 165),
  ('解剖部位', '头', 173, 174),
  ('疾病和诊断', '慢性阻塞性肺病急性加重', 250, 261)],
 [('疾病和诊断', '腹腔积液', 118, 122),
  ('实验室检验', '白蛋白', 161, 164),
  ('实验室检验', '凝血酶时间', 249, 254),
  ('实验室检验', 'AST', 171, 174),
  ('实验室检验', 'PT', 228, 230),
  ('疾病和诊断', '急性胆囊炎', 106, 111),
  ('疾病和诊断', '急性胆囊炎', 264, 269),
  ('实验室检验', '白细胞', 127, 130),
  ('实验室检验', 'GGT', 182, 185),
  ('影像检查', '彩超', 88, 90),
  ('解剖部位', '主胰管', 112, 115),
  ('实验室检验', 'TBIL', 193, 197),
  ('实验室检验', 'DBIL', 208, 212),
  ('解剖部位', '下腹部', 14, 17),
  ('实验室检验', '纤维蛋白原', 236, 241),
  ('实验室检验', '中性粒细胞', 143, 14

观察结果

In [87]:
for sen, true, pre in zip(sentences, y_true, y_pre):
    print("".join(sen))
    print('-*-'*40)
    # 真实标签里有而预测结果里没有的（影响Recall）
    print('high:', sorted(list(set(true).difference(set(pre))), key=lambda x: x[2]))
    print('-*-'*40)
    # 预测结果里有而真实标签里没有的（影响Precision）
    print('low:', sorted(list(set(pre).difference(set(true))), key=lambda x: x[2]))
    print('-*-'*40)
    print('high:', sorted(true, key=lambda x: x[2]))
    print('-*-'*40)
    print('low:', sorted(pre, key=lambda x: x[2]))
    print('\n')

，剖宫产术后4月（孕期体重增加20KG），常规产后检查发现宫颈病变，2014.1.29因宫颈癌行手术治疗（广泛子宫全切+腹主动脉旁淋巴结取样+盆腔淋巴结切除+两侧卵巢悬吊）。，我院会诊病理：中分化鳞状细胞癌，可见脉管癌栓，浸润深度1.4CM，累及宫颈，淋巴结无转移。患者现术后恢复良好，现大小便正常。，14-3-5盆腹MRI：阴道残端左下方不规则信号，大网膜及腹膜弥漫增厚，较大42*28MM。腹膜弥漫增厚转移可能。14-3-10PET-CT复查阴道残端及残端左侧不规则软组织影伴代谢活跃，腹膜考虑非转移，行盆腔放疗，，计划：CTV45GY/25F，2014-3-27开始放疗，放疗7次，大便次数多，2-3次/天。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('疾病和诊断', '剖宫产术后', 1, 6)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('解剖部位', '宫颈', 29, 31), ('疾病和诊断', '宫颈癌', 44, 47), ('手术', '广泛子宫全切+腹主动脉旁淋巴结取样+盆腔淋巴结切除+两侧卵巢悬吊', 53, 85), ('疾病和诊断', '中分化鳞状细胞癌', 95, 103), ('解剖部位', '宫颈', 123, 125), ('影像检查', '盆腹MRI', 157, 162), ('解剖部位', '阴道', 163, 165), ('解剖部位', '腹', 180, 181), ('解剖部位', '腹', 197, 198), ('影像检查', 'PET-CT

high: [('解剖部位', '面', 87, 88), ('解剖部位', '肢体', 88, 90), ('解剖部位', '腹', 93, 94), ('疾病和诊断', '消化道出血原因待查✄', 118, 128), ('疾病和诊断', '胃体', 216, 218), ('疾病和诊断', '下消化道出血原因', 239, 247)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('解剖部位', '颜面', 86, 88), ('疾病和诊断', '消化道出血原因待查', 118, 127), ('解剖部位', '胃体', 216, 218), ('疾病和诊断', '静脉曲张', 226, 230), ('疾病和诊断', '下消化道出血原因不能明确', 239, 251)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('药物', '头痛粉', 9, 12), ('解剖部位', '头', 36, 37), ('解剖部位', '腹', 63, 64), ('解剖部位', '腹', 66, 67), ('解剖部位', '腹', 69, 70), ('解剖部位', '口', 83, 84), ('解剖部位', '面', 87, 88), ('解剖部位', '肢体', 88, 90), ('解剖部位', '腹', 93, 94), ('实验室检验', 'Hb', 103, 105), ('疾病和诊断', '消化道出血原因待查✄', 118, 128), ('疾病和诊断', '重度贫血', 130, 134), ('疾病和诊断', '丙肝肝硬化', 136, 141), ('疾病和诊断', '胃底静脉曲张', 196, 202), ('疾病和诊断', '胃体', 216, 218), ('疾病和诊断', '十二指肠球炎', 231, 237), ('疾病和诊

low: [('疾病和诊断', '胃癌并肝转移', 14, 20), ('手术', '全胃切除术', 24, 29), ('疾病和诊断', '（胃）中低分化腺癌', 39, 48), ('解剖部位', '食管', 105, 107), ('解剖部位', '小弯侧淋巴结', 114, 120), ('解剖部位', '大弯侧淋巴结', 139, 145), ('药物', '奥沙利铂', 256, 260), ('药物', '替吉奥', 269, 272), ('药物', '多西他赛', 303, 307), ('药物', '卡培他滨', 308, 312), ('药物', '多西他赛', 327, 331), ('药物', '卡培他滨', 340, 344), ('影像检查', 'CT', 368, 370), ('疾病和诊断', '胃CA治疗后', 371, 377), ('解剖部位', '左肺门淋巴结', 380, 386), ('疾病和诊断', '肝脏多发转移', 387, 393), ('解剖部位', '两肺', 402, 404), ('解剖部位', '纵隔淋巴结', 422, 427), ('疾病和诊断', '左肺局限性炎症', 431, 438), ('解剖部位', '两肺', 439, 441), ('疾病和诊断', '右肾多发囊肿', 445, 451), ('疾病和诊断', '腹腔及盆腔积液', 452, 459), ('药物', '伊立替康', 462, 466), ('药物', '顺铂', 467, 469), ('药物', '伊立替康', 482, 486), ('药物', '顺铂', 495, 497), ('疾病和诊断', '神经性头痛', 564, 569)]


，1月前无明显诱因出现腹泻稀薄便，便末带少量鲜血，下午为着，日4-5次，里急后重感明显，无腹痛，无恶心呕吐，无“痔疮”病史，2012-7-9，我院门诊肠镜示：距肛门8-12CM直肠见菜花样肿物，病变累及1/2圈，，活检病理示：中分化腺癌；2012-7-11，盆腔MRI提示：直肠中下段占位，考虑直肠癌，侵透浆膜；直肠系膜、直肠下动脉旁、两侧髂血管旁多发淋巴结，转移可能大。，胸部CT示：两肺多发结节结节灶，考虑转移可能大，右上肺原发灶不能除外；肝脏多发低密度灶，考虑囊肿。，CEA:

low: [('实验室检验', '血糖', 12, 14), ('药物', '格列美脲片', 23, 28), ('药物', '阿卡波糖', 36, 40), ('实验室检验', '血糖', 52, 54), ('解剖部位', '腰', 68, 69), ('影像检查', '腰椎MRI', 81, 86), ('疾病和诊断', '腰2椎体轻度压缩性骨折', 87, 98), ('解剖部位', '腰4椎体', 99, 103), ('疾病和诊断', '骶管囊肿', 117, 121), ('解剖部位', '腰椎', 127, 129), ('疾病和诊断', '腰2、腰4椎体压缩性骨折', 151, 163), ('疾病和诊断', '重度骨质疏松症', 164, 171), ('解剖部位', '腰', 212, 213), ('解剖部位', '头', 218, 219), ('解剖部位', '腰', 226, 227), ('解剖部位', '腰', 237, 238), ('解剖部位', '头', 253, 254), ('解剖部位', '胸', 264, 265), ('解剖部位', '胸', 267, 268), ('解剖部位', '腹', 278, 279), ('解剖部位', '腹', 281, 282), ('解剖部位', '肢体', 292, 294)]


患者于2小时前被家属发现意识模糊，阵性胡言乱语，无法交流，无恶心、呕吐、发热、气促、呼吸困难、抽搐及大小便失禁等。家属将其送入我院急诊科查指血糖2.1mmol/l，血压216/98mmHg，头颅CT提示右侧基底节腔隙性脑梗死；两侧脑室体旁及半卵圆中心脱髓鞘改变；脑萎缩。血常规：白细胞数✄4.6✄10^9/L、血红蛋白浓度✄109✄g/L、中性粒细胞百分比✄75.31✄%，电解质：钾✄3.24✄mmol/l。心肌酶谱、肌钙蛋白、肾功等大致正常。予静推“50%葡萄糖✄40ml”、静滴“神经节甘酯”后逐渐清醒，血糖升至6.7mmol/l，送入我科住院治疗。患者此次患病以来精神食欲差，大小便正常，睡眠尚可，体力明显上降，体重无明显改变。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--

，患者3周前因在我院确诊“胃癌”于2015-09-25全麻上行\"胃癌根治术\"（远端胃大部切除），术程顺利，术后预防感染、抑制分泌、静脉营养等对症支持处理，恢复好，切口甲级愈合。，术后病理示：“（胃大体）镜检为低分化腺癌，LAUREN，分型：弥漫型，浸润至浆膜层，可见神经束侵犯，未见脉管内癌栓；网膜组织未见癌。LN+（0/36）；PT3N0M0,IIA期）。”，后于10-16日行术后第一程化疗，，方案为：S1单药。化疗程中，副反应可耐受，间中复查血常规、肝肾功能结果基本正常。现为行第二程化疗收入我科。起病以来，患者精神尚可，食欲欠佳，大小便正常，身体无明显消瘦。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('手术', '胃癌根治术\\"（远端胃大部切除）', 33, 49)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('手术', '胃癌根治术', 33, 38), ('手术', '远端胃大部切除', 41, 48), ('疾病和诊断', '低分化腺癌，LAUREN，分型：弥漫型', 106, 125), ('解剖部位', '肝', 230, 231), ('解剖部位', '肾', 231, 232)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('疾病和诊断', '胃癌', 13, 15), ('手术', '胃癌根治术\\"（远端胃大部切除）', 33, 49), ('解剖部位', '胃', 99, 100), ('疾病和诊断', '低分化腺癌', 106, 111), ('药物', 'S1', 205, 207)]
-*--*--*

...

low: [('疾病和诊断', '食管胃交界部腺癌', 19, 27), ('手术', '根治性全胃切除+食管-空肠ROUX-EN-Y吻合术', 31, 56), ('解剖部位', '腹', 64, 65), ('解剖部位', '肝脏', 67, 69), ('解剖部位', '腹腔', 86, 88), ('解剖部位', '腹', 91, 92), ('解剖部位', '空回肠', 95, 98), ('解剖部位', '贲门', 105, 107), ('疾病和诊断', '贲门癌', 117, 120), ('手术', '贲门癌根治术', 129, 135), ('解剖部位', '胃', 145, 146), ('解剖部位', '肠', 146, 147), ('解剖部位', '肠', 157, 158), ('解剖部位', '胃', 187, 188), ('疾病和诊断', '食管胃交界早期浅表隆起型（0-IIA型，肿瘤主体位于胃）管状腺癌II级', 191, 226), ('疾病和诊断', '黏液腺癌', 230, 234), ('解剖部位', '贲门周淋巴结', 270, 276), ('解剖部位', '小弯侧淋巴结', 281, 287), ('解剖部位', '大弯侧淋巴结', 292, 298), ('解剖部位', '腹腔', 319, 321), ('解剖部位', '胃肠', 335, 337), ('疾病和诊断', '根治性全胃切除术+食管-空肠吻合术后', 338, 356), ('手术', '腹腔引流', 363, 367), ('药物', '舒普深', 368, 371), ('药物', '甲硝唑', 373, 376), ('解剖部位', '消化道', 388, 391), ('药物', '泰素', 422, 424), ('药物', '顺铂', 437, 439), ('解剖部位', '肝', 467, 468), ('解剖部位', '胃', 470, 471), ('疾病和诊断', '骨髓抑制', 508, 512), ('实验室检验', '白细胞', 513, 516), ('实验室检验', '血红蛋白', 529, 533), ('实验室检验', '血小板', 541, 544), ('实验室检验', '白细胞', 563, 566), 

high: [('解剖部位', '下腹部', 2, 5), ('疾病和诊断', '胃窦巨大溃疡', 12, 18), ('疾病和诊断', '中分化腺癌', 22, 27), ('影像检查', '腹部CT', 29, 33), ('解剖部位', '肝脏', 36, 38), ('解剖部位', '腹腔淋巴结', 43, 48), ('实验室检验', 'CEA✄', 56, 60), ('药物', '赫赛汀', 88, 91), ('药物', '吡咯替尼', 113, 117), ('影像检查', 'CT', 144, 146), ('影像检查', '腹盆CT', 166, 170), ('解剖部位', '胃窦部', 181, 184), ('解剖部位', '胃', 184, 185), ('解剖部位', '胃周淋巴结', 221, 226), ('解剖部位', '胃角', 237, 239), ('解剖部位', '胃', 243, 244), ('解剖部位', '胃', 258, 259), ('解剖部位', '胰腺', 265, 267), ('解剖部位', '肝胃韧带', 274, 278), ('解剖部位', '腹腔', 293, 295), ('解剖部位', '腹', 296, 297), ('疾病和诊断', '盆腔积液', 351, 355), ('疾病和诊断', '肝多发转移', 360, 365)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('解剖部位', '下腹部', 2, 5), ('疾病和诊断', '胃窦巨大溃疡', 12, 18), ('疾病和诊断', '中分化腺癌', 22, 27), ('影像检查', '腹部CT', 29, 33), ('解剖部位', '肝脏', 36, 38), ('解剖部位', '腹腔淋巴结', 43, 48), ('实验室检验', 'CEA', 56, 59), ('药物', '赫赛汀', 88, 91), ('药物', '吡咯替尼', 113, 117), ('影像检查', 'CT', 144, 146), 

high: [('解剖部位', '腹', 8, 9), ('疾病和诊断', '肝硬化', 14, 17), ('解剖部位', '腹', 27, 28), ('解剖部位', '腹', 36, 37), ('疾病和诊断', '肝性脑病', 56, 60), ('手术', '重度食管静脉曲张套扎治疗+组织粘合剂', 138, 156), ('解剖部位', '头', 180, 181), ('解剖部位', '腹', 187, 188), ('解剖部位', '腹', 189, 190), ('药物', '呋塞米片', 208, 212), ('药物', '螺内酯', 217, 220), ('疾病和诊断', '肝硬化失代偿胃底静脉曲张治疗术后', 258, 274)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('解剖部位', '腹', 8, 9), ('疾病和诊断', '肝硬化', 14, 17), ('解剖部位', '腹', 27, 28), ('解剖部位', '腹', 36, 37), ('疾病和诊断', '肝性脑病', 56, 60), ('解剖部位', '头', 180, 181), ('解剖部位', '腹', 187, 188), ('解剖部位', '腹', 189, 190), ('药物', '呋塞米片', 208, 212), ('药物', '螺内酯', 217, 220), ('疾病和诊断', '肝硬化失代偿胃底静脉曲张治疗术后', 258, 274)]


患者2015-03因左侧股动脉假性动脉瘤于我院就诊，行左上肢截肢手术。术后患者定期复查，于2016-02-26查腹部血管CTA提示：腹主动假性动脉瘤，右侧髂总动脉起始处管腔狭窄；右肾动脉假性动脉瘤。患者偶有上腹部隐痛，有排尿、排便不尽感，无恶心呕吐，无呕血便血黑便，无头痛头晕、黑朦晕厥，四肢感觉活动可。患者现为行进一步诊疗收入病房。病程中，患者神清，精神可，食欲睡眠可，二便无殊，体重无明显变化。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*

high: [('解剖部位', '咽', 34, 35), ('解剖部位', '胸', 40, 41), ('解剖部位', '胸', 161, 162), ('解剖部位', '胸', 231, 232), ('疾病和诊断', '慢性支气管炎急性发作', 250, 260), ('解剖部位', '头', 317, 318), ('解剖部位', '头', 320, 321), ('解剖部位', '胸', 340, 341), ('解剖部位', '胸', 343, 344), ('解剖部位', '右肩肩背背部', 356, 362), ('解剖部位', '胸', 422, 423), ('解剖部位', '背部', 458, 460), ('解剖部位', '右上肢', 461, 464), ('解剖部位', '关节', 506, 508)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('解剖部位', '咽', 34, 35), ('解剖部位', '胸', 40, 41), ('解剖部位', '胸', 161, 162), ('解剖部位', '胸', 231, 232), ('疾病和诊断', '慢性支气管炎急性发作', 250, 260), ('解剖部位', '头', 317, 318), ('解剖部位', '头', 320, 321), ('解剖部位', '胸', 340, 341), ('解剖部位', '胸', 343, 344), ('解剖部位', '右肩肩背背部', 356, 362), ('解剖部位', '胸', 422, 423), ('解剖部位', '背部', 458, 460), ('解剖部位', '右上肢上臂背侧', 461, 468), ('解剖部位', '关节', 506, 508)]


患者近4.5年前无明显诱因出现左上腹坠痛，同时伴有大便性状改变，形状变细，大便带血，呈暗红色，大便次数无明显改变，行肠镜示肿瘤可能性大，遂于我院普外科行根治性左半结肠切除术，术中见肿物6*7厘米，侵透浆膜，术后病理示印戒细胞癌，断端未见癌。手术后无明显不适。后

low: [('解剖部位', '盆腔', 23, 25), ('疾病和诊断', '卵巢CA？', 28, 33), ('疾病和诊断', '糖尿病', 37, 40), ('手术', '剖腹探查+全子宫两附件切除+大网膜切除+阑尾切除+放射性粒子置入术', 46, 79), ('解剖部位', '右侧附件', 85, 89), ('解剖部位', '宫底', 146, 148), ('解剖部位', '乙状结肠', 149, 153), ('解剖部位', '子宫', 167, 169), ('解剖部位', '子宫底', 172, 175), ('解剖部位', '左侧输卵管', 184, 189), ('解剖部位', '左卵巢', 196, 199), ('解剖部位', '盆腔', 210, 212), ('解剖部位', '腹', 212, 213), ('解剖部位', '右附件', 233, 236), ('疾病和诊断', '（右附件）卵巢浆液性乳头状囊腺癌', 252, 268), ('解剖部位', '输卵管', 270, 273), ('手术', '子宫、左侧附件、大网膜、阑尾切除术', 277, 294), ('疾病和诊断', '浆液性乳头状囊腺癌', 320, 329), ('解剖部位', '子宫', 332, 334), ('解剖部位', '宫腔', 343, 345), ('解剖部位', '宫颈', 346, 348), ('解剖部位', '右附件', 349, 352), ('解剖部位', '阑尾', 365, 367), ('药物', '顺铂', 382, 384), ('解剖部位', '腹腔', 389, 391), ('药物', '紫杉醇', 400, 403), ('药物', '紫杉醇', 444, 447), ('药物', '特素', 448, 450), ('药物', '奥沙利铂', 457, 461)]




规则：

    1.限制长度的词表匹配（实验室检验，药物，影像检查，疾病与诊断，手术，解剖部位）
    2.白细胞（数），幽门[部]，[始]善龙，（全）子宫，胸骨（后），心[肺]，宫颈（部），血小板（数），子宫（内膜），（右侧）腹腔，肠（壁），肠（腔）

## 规则

词表匹配

In [124]:
data_dir = ['../data/train/']
sentences = []
tags = []
for dir_ in data_dir:
    with open(dir_+'sentences.txt', 'r', encoding='utf-8') as f_sen,\
        open(dir_+'tags.txt', 'r', encoding='utf-8') as f_tag:
        sentences.extend([line.strip().split(' ') for line in f_sen])
        tags.extend([line.strip().split(' ') for line in f_tag])

In [132]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con)))
    y_true.extend(sample) 

In [133]:
y_true[0]

('解剖部位', '中下腹')

In [134]:
with open('./ne_vocab.txt', 'r', encoding='utf-8') as f:
    y_true.extend([(line.strip().split('\t')[1], line.strip().split('\t')[0]) for line in f])

In [135]:
y_true[-1]

('解剖部位', '胃小弯侧')

In [136]:
with open('./whole_vocab.txt', 'w', encoding='utf-8') as f:
    for line in set(y_true):
        f.write(f'{line[0]}\t{line[1]}\n')

In [137]:
y_true = list(set(y_true))

In [138]:
import pandas as pd
df = pd.DataFrame({
    "type": [ne[0] for ne in y_true],
    "content": [ne[1] for ne in y_true]
})
df['length'] = df.apply(lambda row: len(row.content), axis=1)

In [139]:
df

type                      content  length
0        药物                        铝碳酸镁片       5
1     疾病和诊断  恶性肿瘤，食管癌可能大，并右侧锁骨下上、纵膈淋巴结转移      27
2        药物                          佩乐能       3
3     实验室检验                         癌胚抗原       4
4      解剖部位                          阴道口       3
...     ...                          ...     ...
8388     手术     超声引导下右侧腋窝肿块、双侧锁骨上肿块穿刺活检术      24
8389  疾病和诊断                 直肠癌（MILES）术后      12
8390  疾病和诊断         胃体胃窦癌(CT4N2M0,IIIB期)      20
8391   解剖部位                         左侧腰部       4
8392  疾病和诊断                       胃内多发息肉       6

[8393 rows x 3 columns]

In [140]:
df_gb = df.groupby('type')

实验室检验

In [144]:
df_lab = df.iloc[df_gb.groups['实验室检验']]
df_lab

type                           content  length
3     实验室检验                              癌胚抗原       4
25    实验室检验                            CA-125       6
30    实验室检验                             白细胞计数       5
58    实验室检验                               胆红素       3
59    实验室检验                              A/，G       4
...     ...                               ...     ...
8337  实验室检验                            外周血白细胞       6
8342  实验室检验                            甲状旁腺激素       6
8346  实验室检验                            CA 199       6
8354  实验室检验                              大便常规       4
8355  实验室检验  抗甲状腺过氧化物酶抗体(Anti-TPO)(ANTI-TPO)✄      32

[441 rows x 3 columns]

In [158]:
df_lab = df_lab.drop([3732])

In [161]:
df_lab[df_lab.length==1]

type content  length
616   实验室检验       N       1
860   实验室检验       氯       1
2618  实验室检验       e       1
4434  实验室检验       K       1
5053  实验室检验       钾       1
5098  实验室检验       钠       1
6512  实验室检验       L       1
7821  实验室检验       钙       1
8066  实验室检验       磷       1

In [163]:
df_lab = df_lab.drop(df_lab[df_lab.length==1].index)

In [164]:
df_lab

type                           content  length
3     实验室检验                              癌胚抗原       4
25    实验室检验                            CA-125       6
30    实验室检验                             白细胞计数       5
58    实验室检验                               胆红素       3
59    实验室检验                              A/，G       4
...     ...                               ...     ...
8337  实验室检验                            外周血白细胞       6
8342  实验室检验                            甲状旁腺激素       6
8346  实验室检验                            CA 199       6
8354  实验室检验                              大便常规       4
8355  实验室检验  抗甲状腺过氧化物酶抗体(Anti-TPO)(ANTI-TPO)✄      32

[431 rows x 3 columns]

药物

In [151]:
df_med = df.iloc[df_gb.groups['药物']]
df_med

type    content  length
0      药物      铝碳酸镁片       5
2      药物        佩乐能       3
13     药物       胸部切口       4
23     药物        巴曲酶       3
45     药物     复方黄松洗液       6
...   ...        ...     ...
8338   药物      脑络通胶囊       5
8341   药物  卡培他滨（希罗达）       9
8348   药物       阿那曲唑       4
8349   药物         类克       2
8357   药物        新癀片       3

[1028 rows x 3 columns]

In [149]:
df_scr = df.iloc[df_gb.groups['影像检查']]
df_scr

type          content  length
15    影像检查           PET-CT       6
47    影像检查            肝脏MRI       5
56    影像检查            胸部CT提       5
125   影像检查             颅脑ct       4
145   影像检查            肺部CTA       5
...    ...              ...     ...
8224  影像检查             盆腔ct       4
8245  影像检查            肝脏MRS       5
8311  影像检查             颈部超声       4
8372  影像检查  胸部、下腹、上腹部、盆腔，CT      15
8379  影像检查           腹盆部，CT       6

[321 rows x 3 columns]

In [152]:
df_med[df_med.length==1]

type content  length
544    药物       姜       1
1495   药物       豉       1
2874   药物       苹       1
4586   药物       柏       1

## 测试集结果

In [16]:
ex1_dir = Path('../ensemble/fusion_submit.txt')
with open(ex1_dir, 'r', encoding='utf-8') as f:
    pre = [json.loads(line.strip()) for line in f]

In [17]:
y_pre = []
for s in pre:
    text = s['originalText']
    entities = s['entities']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [18]:
for s, p in zip(pre, y_pre):
    print(s['originalText'])
    print('-*-'*40)
    print('-*-'*40)
    print(sorted(p, key=lambda x: x[2]))
    print('\n')

11月前，患者无诱因突发呕吐暗红色血液，含血凝块，解柏油样糊状便，呕血及黑便量不详，无腹痛、腹胀，无发热及皮肤巩膜黄染，无意识障碍，无厌油，急诊于*****医院住院治疗，行胃镜提示“食管静脉曲张”，余检查结果（血图、乙肝病毒标志物、腹部彩超等）不详，诊断为“酒精性肝硬化失代偿”，予以输血治疗（红细胞悬液4u），余治疗方案不详，治疗好转后出院，出院后间断口服药物治疗（具体用药不详）。5月前，患者再发呕吐暗红色血液及解柏油样大便，量不详，遂再次于当地医院住院，予以输血等治疗（具体方案不详）后好转，转入我院感染科住院治疗，行胃镜提示“食管静脉曲张，红色征阳性，慢性浅表性胃炎，十二指肠球部息肉”，腹部ct提示“肝硬化，门脉高压、脾大”，乙肝表面抗体阴性，丙肝抗体阴性，诊断为“上消化道出血，酒精性肝硬化失代偿期，原发性腹膜炎”，经抑酸（泮托拉唑）、降门脉压（奥曲肽）、卡洛磺纳止血、哌拉西林他唑巴坦抗感染、补液支持等治疗后好转，建议其行内镜下食管曲张静脉套扎治疗，患者拒绝，出院后仍间断自服药物治疗（具体药名不详），病情较稳定。1天前，患者无诱因突发呕血，共5次，每次量约200-300ml，暗红色，含血凝块，解柏油样大便1次，糊状，量约100g，伴身黄及尿黄，无厌油及纳差，无酱油色样小便，伴乏力，无反酸、嗳气，无腹痛、腹胀，无发热及畏寒，于*****医院住院治疗，输入红细胞悬液4u治疗，余治疗方案不详，治疗后患者未再呕血及黑便，为进一步治疗，故来我院。\u0004患者自起病以来，精神可，胃纳可，大便如上述，小便如常，体重未见明显下降。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '腹', 43, 44), ('解剖部位', '腹', 46, 47), ('解剖部位', '巩膜', 55, 57), ('疾病和诊断', '食管静脉

[('解剖部位', '阴道', 19, 21), ('解剖部位', '左下腹', 37, 40), ('解剖部位', '腰骶部', 43, 46), ('解剖部位', '头', 60, 61), ('解剖部位', '头', 63, 64), ('解剖部位', '阴道', 89, 91), ('解剖部位', '腰骶部', 114, 117), ('解剖部位', '头', 123, 124), ('解剖部位', '头', 126, 127), ('手术', '宫颈活检', 186, 190), ('解剖部位', '阴道', 194, 196), ('解剖部位', '阴道', 206, 208), ('疾病和诊断', '宫颈鳞癌，低分化', 246, 254), ('疾病和诊断', '宫颈鳞癌iiib期', 258, 267), ('解剖部位', '阴道', 325, 327), ('解剖部位', '盆腔', 401, 403), ('解剖部位', '盆腔淋巴结', 438, 443), ('药物', '奈达铂', 484, 487), ('解剖部位', '阴道', 506, 508), ('解剖部位', '阴道', 522, 524), ('解剖部位', '阴道', 555, 557), ('解剖部位', '阴道', 566, 568), ('疾病和诊断', '宫颈癌化疗后', 581, 587)]


20年1986年患者无意间被电击伤，随即昏迷、意识丧失，伴双上肢前臂近腕关节处“铜钱”大小烧灼坏死区；左前臂背侧坏死区，可见少量黄色脓性分泌物，左侧腕关节活动受限，伴双侧腋窝、双侧手掌畸形双下肢踝关节、后方、外侧及足背区“巴掌”大小烧灼坏死区；双下肢活动障碍。遂就诊于“*****医院”当时给予补液等及手术治疗，截除右侧腓骨及右足第一足趾。自诉好转出院，于1986年因无意间致左侧踝关节后外侧及足背结痂脱落，未予处理，自诉伤口可见黄白色脓性渗出，右足第足趾坏死，遂就诊于“***昆明总医院”行“左下肢溃疡区扩大切除术+取皮植皮术+右足第二足趾截趾术。”取皮区为右大腿前方中段，术后给予对症支持治疗；术后植皮区未愈；截趾区愈合。患者自动要求出院，自行消毒处理，效果不明显，于2011年因植皮区坏死感染就诊于“*****医院”再次行左足溃疡区“病灶扩大切除术+取皮植皮术”，术后给予对

[('解剖部位', '双侧膝关节', 15, 20), ('解剖部位', '双下肢', 45, 48), ('疾病和诊断', '过敏性紫癜', 110, 115), ('药物', '甲强龙', 119, 122), ('解剖部位', '膝关节', 143, 146), ('药物', '泼尼松', 162, 165), ('药物', '泼尼松', 211, 214), ('解剖部位', '膝关节', 227, 230), ('解剖部位', '腹', 242, 243), ('解剖部位', '脐周', 246, 248), ('解剖部位', '腹', 281, 282), ('药物', '泼尼松', 299, 302), ('药物', '泼尼松', 342, 345), ('解剖部位', '关节', 352, 354), ('解剖部位', '腹', 356, 357), ('药物', '泼尼松', 372, 375), ('解剖部位', '双侧膝关节', 386, 391), ('解剖部位', '踝关节关节', 392, 397), ('解剖部位', '腹', 410, 411), ('药物', '泼尼松', 453, 456), ('药物', '泼尼松', 478, 481), ('解剖部位', '膝关节', 496, 499), ('解剖部位', '腹', 506, 507), ('疾病和诊断', '膝关节疼痛待查', 573, 580)]


患者10余年前因发现夜间睡眠呼吸暂停，予呼吸机家庭氧疗（具体不详），后患者自觉不适遂停用。近数月来患者出现精神差，晨起乏力，伴头晕头痛及记忆力下降，轻度嗜睡，亲友诉患者夜间打鼾，有长时间呼吸暂停，无咳嗽、咳痰、咯血、呼吸困难、发冷、发热、盗汗。2014-11-10我科住院行睡眠呼吸监测：睡眠呼吸暂停低通气综合征（阻塞型，重度），夜间睡眠低氧血症（重度）。进一步行呼吸机治疗监测：患者本次治疗人机配合较好，呼吸机压力稳定，平均血氧饱和度为96%，建议长期使用呼吸机治疗，门诊随访。出院后患者未用呼吸机治疗，无头晕、乏力等不适，家中自测指尖氧饱和度92%-93%，现为进一步治疗收入我科。发病以来，患者胃**，睡眠不佳，两便无殊，体重无明显变化。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*

[('解剖部位', '上腹部', 10, 13), ('疾病和诊断', '胃癌', 40, 42), ('解剖部位', '胃', 76, 77), ('解剖部位', '胃窦', 81, 83), ('解剖部位', '幽门', 84, 86), ('解剖部位', '肝脏左外叶', 104, 109), ('解剖部位', '横结肠', 110, 113), ('解剖部位', '肝十二指肠韧带', 120, 127), ('解剖部位', '胃小弯区', 128, 132), ('解剖部位', '淋巴结', 134, 137), ('手术', '远端胃癌根治术+roux-y吻合术', 141, 158), ('疾病和诊断', '胃及大网膜管状腺癌', 183, 192), ('解剖部位', '胃', 202, 203), ('解剖部位', '胃', 219, 220), ('解剖部位', '胃小弯侧淋巴结', 231, 238), ('解剖部位', '第八组淋巴结', 247, 253), ('解剖部位', '大弯侧淋巴结', 267, 273), ('疾病和诊断', '骨髓抑制', 329, 333), ('实验室检验', '血小板', 336, 339), ('药物', '卡培他滨', 358, 362), ('药物', '卡培他滨', 413, 417), ('疾病和诊断', '胃癌术后', 456, 460)]


3月前患者查：胸正位：右上肺淡薄斑片影，排除禁忌后于2015.4.23行胸腔镜下右中肺叶切除+术中冰冻病理检查+淋巴结清扫术，术程顺利，安返病房。术后病理提示：低分化腺癌，内未见癌转移（0/23）。现术后恢复可。2015-06-13，“右肺癌”为化疗入院，排除化疗禁忌后于2015-6-17行第1次术后化疗，具体为“培美曲塞二钠(赛珍)针760mg+[进口]顺铂针100mg”，于2015-7-6行第二次化疗，方案为“培美曲塞二钠(赛珍)针800mg+[进口]顺铂针100mg”，辅以护胃止吐等治疗。过程顺利。今为行第3次化疗入院。现一般情况可，无胸闷气急，无咳嗽咳痰，为化疗，拟“右肺癌”收住入院。自病以来，神清，精神可，胃纳可，睡眠一般，二便无殊，体重无明显减轻。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*

-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '咽', 20, 21), ('解剖部位', '胸', 149, 150), ('解剖部位', '胸', 165, 166), ('解剖部位', '心', 186, 187), ('解剖部位', '双下肢', 193, 196), ('药物', '青霉素', 233, 236), ('药物', '头孢', 237, 239), ('解剖部位', '腹部', 266, 268), ('影像检查', '胸片', 300, 302), ('解剖部位', '双肺', 303, 305), ('疾病和诊断', '咳嗽急性支气管炎', 318, 326)]


患者10月前（2015-03）无明显诱因于夜间睡眠时突发胸痛，无伴胸闷、气促，无心悸、出冷汗等不适，持续5-6分钟后即缓解，当时未至医院就诊。2015-04患者再次发作夜间胸痛，症状及性质同前，后至当地医院行心电图检查示“正常心电图”（未见报告），当地医院予阿司匹林、泰嘉抗血小板，瑞舒伐他汀调脂稳定斑块，单硝酸异山梨酯扩冠营养心肌（患者诉因担心消化道出血，未服用阿司匹林），其余药物规律服用，无再出现胸痛等不适。2016-01-12患者解便时（自诉稍用力）再次突发胸痛，程度较前剧烈，持续10-15分钟后缓解，至**********医院就诊，心电图检查示：窦性心动过速，ii、iii、avf导联q波；心肌酶谱、肌钙蛋白、bnp正常；d-二聚体：624ug/l↑（0-550ug/l）；甲状腺功能、肿瘤标志物无殊。患者为进一步诊治至我院就诊，2016-01-14心电图示：窦性心律（82bpm）；ii、iii、avf导联q波。考虑为“冠心病、心绞痛”，为进一步行冠脉造影收住入院。病程中，患者精神、胃纳、睡眠尚可，大小便无殊，未解过黑便，近期体重无明显改变。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-

...

[('疾病和诊断', '炎症性肠病', 39, 44), ('疾病和诊断', '小肠血管畸形并出血', 45, 54), ('实验室检验', '尿蛋白', 88, 91), ('实验室检验', '尿酮体', 94, 97), ('实验室检验', '尿潜血', 100, 103), ('实验室检验', '白细胞', 106, 109), ('实验室检验', '红细胞', 115, 118), ('实验室检验', '鳞状上皮细胞', 125, 131), ('实验室检验', '白细胞', 161, 164), ('实验室检验', '脓细胞', 167, 170), ('实验室检验', '隐血', 172, 174), ('实验室检验', '血浆凝血酶原时间活动度', 191, 202), ('实验室检验', '血浆纤维蛋白原测定', 209, 218), ('实验室检验', '白细胞计数', 247, 252), ('实验室检验', '中性粒细胞', 265, 270), ('实验室检验', '平均血红蛋白浓度', 284, 292), ('实验室检验', '谷丙转氨酶', 325, 330), ('实验室检验', '谷草转氨酶', 337, 342), ('实验室检验', '前白蛋白', 350, 354), ('实验室检验', '氯', 364, 365), ('实验室检验', '同型半胱氨酸', 374, 380), ('实验室检验', 'c反应蛋白', 409, 414), ('影像检查', '心电图', 424, 427), ('疾病和诊断', '窦性心律', 440, 444), ('影像检查', '心电图', 450, 453), ('疾病和诊断', '消化道肿瘤', 459, 464), ('解剖部位', '肠', 510, 511), ('疾病和诊断', '回肠末端溃疡', 558, 564), ('疾病和诊断', '克隆恩病', 568, 572), ('解剖部位', '回肠末端', 588, 592), ('疾病和诊断', '轻度急慢性发炎', 603, 610), ('疾病和诊断', '克罗恩病', 616, 620), ('药物', '柳氮磺吡啶片', 626, 632), ('解剖部位', '腹部', 651, 653), ('影像检查', 

1年前，患者因发现右乳包块到我院就诊，包块大小约3*2cm，质地硬，活动度差，边界欠清，伴轻度压痛，遂于我院行“右乳包块穿刺活检术”，术后病检提示（1304039）：&lt;右乳&gt;恶性肿瘤，倾向浸润性导管癌。于我院普外科行tac方案化疗5次，化疗期间有恶心、呕吐等不适，并监测血常规等提示骨髓抑制，予以止吐、升白等治疗后好转。之后于2014-03-27在全麻下行“右乳腺癌根治术及改良根治术”，术后恢复可，术后病检（病理号：1402331）：右乳腺浸润性导管癌（ii级,7分），乳头无癌累及，腋窝淋巴转移（30/31）免疫组化：er（±）pr（-）c-erbb-2（+++）e-ca（+）p53（-）34βe12（-）e-ca（+）ki67（+&gt;40%），术后予以tac化疗2周期，化疗后出院休养。于2014-5月22日行病灶及淋巴引流区imrt（50gy/25f），住院期间监测血常规提示白细胞减少，予以升白治疗后好转。放疗结束后建议患者**化疗，但患者表示拒绝，予以办理出院，之后患者未行其他特殊治疗。2天前于我科门诊复查胸部ct提示：1、“乳腺癌”术后复查：目前右侧乳腺术后缺如。2、双肺多发结节，考虑转移性肿瘤。3、纵隔内多发淋巴结肿大。4、双右侧胸腔积液，并右肺下叶部分肺组织不张。上腹部ct：1、肝内多发病灶，考虑转移性肿瘤。2、肝右叶钙化灶。3、脂肪肝。4、胆囊结石。5、右侧胸腔积液。今患者为行进一步治疗入我科。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '右乳', 9, 11), ('手术', '右乳包块穿刺活检术', 56, 65), ('疾病和诊断', '右乳&gt;恶性肿瘤', 87, 97), ('疾病和诊断', '浸润性导管癌', 100, 106), ('疾病和诊断', '骨髓抑制', 14

患儿4月余前无明显诱因出现咳嗽、气喘，病初有发热，体温最高39℃，伴口唇紫绀，往****医院就诊住院治疗，诊断为重症肺炎，具体治疗不详，患儿住院40余天后病情未见明显好转，遂转入*****医院进一步诊治，住院期间具体治疗不详，住院治疗47天后，患儿病情好转，予出院，但6月13日患儿又出现咳嗽，表现为单声咳，不剧烈，14日出现气喘，立即往*****医院就诊并住院治疗，住院期间2次因病情危重转入该院重症医学科，入院后于6月20-7月8日予亚胺培南西司他丁、替考拉宁、伏立康唑抗感染（具体应用时间、剂量不详），予呼吸机辅助通气（6月20-24日，7月9-16日），头孢哌酮舒巴坦（7月8-19日，7月24-8月1日）抗感染，阿奇霉素（用5天），亚胺培南西司他丁（7月9-22日），伏立康唑（7月8-19日），阿米卡星（7月26-8月1日）抗感染，静脉丙球增强免疫力（7月3、4日6g），多索茶碱，硫酸镁，沙丁胺醇，甲泼尼龙琥珀酸钠平喘，磷酸肌酸护心等对症治疗，患儿病情好转，家长要求上级医院行基因检查，故8月1日带氧出院，出院诊断“重症肺炎并呼吸功能不全、慢性肺疾病、气管软化症、先天性喉软骨发育不全、衣原体感染、巨细胞病毒感染(听力受损）、免疫功能低下、遗传代谢性疾病？轻度贫血”，今来我院就诊，门诊以“肺炎、先天性喉喘鸣、气管软化？遗传代谢病？”收治入院。自生病以来，否认异物吸入史，患儿无皮疹，无呕吐，偶有溢奶，无抽搐、精神反应一般，胃纳欠佳，一周前因腹泻服用腹泻奶粉，每次80ml，q3h，大便日十余次，黄稀糊状，小便量可，睡眠欠佳。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '口唇', 34, 36), ('疾病和诊断', '重症肺炎', 56, 60), ('药物', '亚胺培南西司他丁', 219, 227), ('药物'

患者于2011年7月因发现右侧大腿肿物，大小约6cm，质软，无疼痛，无皮肤发红溃烂，遂前往外院行手术切除（具体不详），术后病理提示“腺泡状软组织肉瘤”，术后未行放化疗或其他抗肿瘤治疗。半年前哺乳时自觉左侧乳房小结节3个，最大者直径约2cm，于外院就诊考虑“良性病变”，予以抗炎治疗3月复查未见明显改变，遂予以行左乳腺结节区段切除，术后病理考虑“乳腺分泌型癌”，患者于**二院行病理会诊提示“转移性肉瘤，形态与左侧大腿肿物一致”，进一步来我院行病理会诊提示：“61756：（右大腿）镜下：瘤细胞细胞核大、嗜酸性核仁明显，胞浆丰富、嗜酸性着色，瘤细胞呈特征性腺泡状排列。病理诊断：（右大腿）腺泡状软组织肉瘤。60076：（左乳腺）镜下：瘤组织形态与61756切片一致，见特征性腺泡状结构。结合临床病史，符合腺泡状软组织肉瘤（左乳腺）转移。”患者近期有咳嗽、咳痰，为白色粘痰。近两日有流清涕，无发热，近期有右侧膝关节及右侧小腿酸麻感，无头痛头晕，无胸痛，气促，呼吸困难，无骨痛。为进一步诊治来我院就诊，门诊行pet/ct检查提示：“右下肢腺泡型软组织肉瘤术后，右下肢代谢未见异常。左侧乳腺数个结节部分局部代谢略活跃，符合转移；左髂骨病灶代谢略活跃，双肺多个小结节代谢未见异常，考虑转移。右肾小囊肿。子宫腔内代谢略活跃，双侧附件区局部代谢略活跃，疑生理性改变。双侧髂骨近骶髂关节面处骨质致密，代谢未见异常，考虑良性病变。”2015.05.29ie方案化疗一程，患者起病以来，无明显发热、盗汗，体重近3月减轻2公斤。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('解剖部位', '右侧大腿', 13, 17), ('疾病和诊断', '腺泡状软组织肉瘤', 66, 74), ('解剖部位', '左侧乳房', 100, 104), ('手术', '左乳腺结节区段切除'

[('解剖部位', '颜面部', 13, 16), ('实验室检验', '蛋白', 42, 44), ('实验室检验', '红细胞', 47, 50), ('实验室检验', '白细胞', 53, 56), ('疾病和诊断', '急性肾小球肾炎', 74, 81), ('实验室检验', '尿蛋白', 104, 107), ('实验室检验', '尿蛋白', 118, 121), ('实验室检验', '潜血', 131, 133), ('解剖部位', '腰', 159, 160), ('解剖部位', '腰', 186, 187), ('解剖部位', '小腹', 189, 191), ('实验室检验', '蛋白', 236, 238), ('实验室检验', '白细胞', 241, 244), ('实验室检验', '潜血', 247, 249), ('疾病和诊断', '泌尿系感染', 261, 266), ('药物', '依替米星', 270, 274), ('解剖部位', '头', 340, 341), ('解剖部位', '头', 343, 344), ('解剖部位', '胸', 347, 348), ('解剖部位', '腹', 354, 355), ('解剖部位', '腹', 357, 358)]


患者于入院前1月余无明显诱因下突发右侧肢体偏瘫，伴无法言语，至外院行头颅ct：左侧大面积脑梗塞。给予营养神经等对症治疗，后为进一步治疗遂至我院就诊，在我院急诊科复查头颅ct：左侧大面积脑梗塞，后患者并发肺炎，给予抗感染、营养神经等治疗，发病来，患者无法言语，偶有指令动作，否认肢体抽搐等不适。我科会诊，急诊拟“左侧大面积脑梗塞”收治入院。入院后完善相关检查，于20140707行下肢血管探查+脑血管造影术，术后诊断：脑血管病：脑梗塞，右侧颈内动脉分叉处动脉瘤。于20140714行脑动脉瘤夹闭术，术后诊断为脑血管病：右侧大脑前动脉a1起始段动脉瘤。目前患者为求进一步诊疗至我院，门诊拟：“脑血管病：脑梗塞；右侧颈内动脉分叉处动脉瘤夹闭术后”收治入院。发病以来，患者神志淡漠、现留置胃管，大小便失禁，体重无明显减轻。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--

## 生成分词自定义词表

In [295]:
with open('./en_freq.txt', 'r', encoding='utf-8') as f:
    data_1 = [line.strip().split('\t') for line in f]

In [296]:
data_1

[['解剖部位', '腹', '2234'],
 ['解剖部位', '胸', '872'],
 ['解剖部位', '头', '708'],
 ['解剖部位', '心', '585'],
 ['解剖部位', '胃', '505'],
 ['解剖部位', '肝', '371'],
 ['解剖部位', '肠', '303'],
 ['影像检查', 'CT', '280'],
 ['药物', '奥沙利铂', '189'],
 ['解剖部位', '阴道', '175'],
 ['解剖部位', '两上肢', '173'],
 ['解剖部位', '肛门', '142'],
 ['解剖部位', '直肠', '141'],
 ['药物', '希罗达', '122'],
 ['解剖部位', '盆腔', '121'],
 ['解剖部位', '腹腔', '115'],
 ['实验室检验', 'CEA', '99'],
 ['疾病和诊断', '胃癌', '98'],
 ['药物', '紫杉醇', '96'],
 ['解剖部位', '四肢', '95'],
 ['解剖部位', '肝脏', '94'],
 ['解剖部位', '子宫', '92'],
 ['疾病和诊断', '直肠癌', '91'],
 ['解剖部位', '下腹部', '91'],
 ['解剖部位', '宫颈', '90'],
 ['解剖部位', '下腹', '88'],
 ['药物', '顺铂', '87'],
 ['解剖部位', '腹部', '85'],
 ['疾病和诊断', '冠心病', '85'],
 ['疾病和诊断', '腺癌', '83'],
 ['药物', '替吉奥', '83'],
 ['实验室检验', '血糖', '81'],
 ['实验室检验', '白细胞', '80'],
 ['影像检查', '心电图', '78'],
 ['解剖部位', '脾', '72'],
 ['解剖部位', '食管', '71'],
 ['解剖部位', '乙状结肠', '71'],
 ['疾病和诊断', '中分化腺癌', '70'],
 ['解剖部位', '上肢', '69'],
 ['影像检查', '腹部CT', '66'],
 ['解剖部位', '胰腺', '64'],
 ['影像检查', '胸片', '64'],
 ['解剖部位'

In [298]:
with open('./ne_vocab.txt', 'r', encoding='utf-8') as f:
    data_2 = [line.strip().split('\t') for line in f]

In [299]:
data_2

[['肝右叶占位病变', '疾病和诊断'],
 ['宫颈鳞癌（IB1期，II级）术后', '疾病和诊断'],
 ['结肠旁沟', '解剖部位'],
 ['高血压病3级极高危组', '疾病和诊断'],
 ['中组淋巴结', '解剖部位'],
 ['总胆汁酸', '实验室检验'],
 ['肾盂输尿管成形', '手术'],
 ['ALT ', '实验室检验'],
 ['高血压心脏病', '疾病和诊断'],
 ['总胆固醇', '实验室检验'],
 ['D-二聚体', '实验室检验'],
 ['肝脏原发性巨块型中分化肝细胞癌', '疾病和诊断'],
 ['食管旁淋巴结', '解剖部位'],
 ['胸9椎体及附件骨质破坏、转移', '疾病和诊断'],
 ['肾性高血', '疾病和诊断'],
 ['肠壁一站（7个）、中间组（6个）淋巴结', '解剖部位'],
 ['右股骨', '解剖部位'],
 ['（胃大弯、小弯）溃疡型中分化管状腺癌', '疾病和诊断'],
 ['舒可捷', '药物'],
 ['谷氨酸脱羧酶抗体阳性', '实验室检验'],
 ['（乙状结肠）腺癌', '疾病和诊断'],
 ['左侧肾静脉', '解剖部位'],
 ['左侧颈动脉中段', '解剖部位'],
 ['肝左后叶', '解剖部位'],
 ['鼻咽、，颈部及下腹部CT', '影像检查'],
 ['伊马替尼', '药物'],
 ['指端', '解剖部位'],
 ['柰达铂', '药物'],
 ['浅表性胃窦炎', '疾病和诊断'],
 ['S4', '解剖部位'],
 ['阿诺新', '药物'],
 ['卵巢腺癌', '疾病和诊断'],
 ['基底部', '解剖部位'],
 ['宫颈鳞癌1B2期', '疾病和诊断'],
 ['横结肠近脾区肠壁', '解剖部位'],
 ['子宫内膜腺癌IIIC期（G3）', '疾病和诊断'],
 ['腹腔镜上根治性全胃切除术+胆囊切除术', '手术'],
 ['FUDR', '药物'],
 ['经腹直肠癌根治术（DIXON术）', '手术'],
 ['海扶刀', '手术'],
 ['腹腔粘连松解', '手术'],
 ['手足综合症', '疾病和诊断'],
 ['子宫内膜非典型增生', '疾病和诊断'],
 ['骨髓', '解剖部位'],
 ['小脑', '解剖部位'],
 [

In [300]:
with open('./custom_vocab.txt', 'w', encoding='utf-8') as f:
    for line in data_1:
        f.write(f'{line[1]} {line[-1]}\n')
    for line in data_2:
        f.write(f'{line[0]}\n')